<h1 align=center><font size = 5>Segmenting and Clustering for Cities in INDIA</font></h1>

## Table of Contents

<div class="alert alert-block alert-info" style="margin-top: 20px">

<font size = 3>

1. <a href="#item1">Download and Explore Dataset</a>

2. <a href="#item2">Explore Neighborhoods in New York City</a>

3. <a href="#item3">Analyze Each Neighborhood</a>

4. <a href="#item4">Cluster Neighborhoods</a>

5. <a href="#item5">Examine Clusters</a>    
</font>
</div>

Before we get the data and start exploring it,  downloaded all the dependencies that we will need.

In [30]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests# library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Solving environment: done

## Package Plan ##

  environment location: /opt/conda/envs/Python36

  added / updated specs: 
    - geopy


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    openssl-1.1.1d             |       h516909a_0         2.1 MB  conda-forge
    geographiclib-1.50         |             py_0          34 KB  conda-forge
    certifi-2019.11.28         |           py36_0         149 KB  conda-forge
    ca-certificates-2019.11.28 |       hecc5488_0         145 KB  conda-forge
    geopy-1.21.0               |             py_0          58 KB  conda-forge
    ------------------------------------------------------------
                                           Total:         2.5 MB

The following NEW packages will be INSTALLED:

    geographiclib:   1.50-py_0         conda-forge
    geopy:           1.21.0-py_0       conda-forge

The following packages will be UPDATED:

    ca-

## 1. Download and Explore Dataset

India have 25 states ( year 2011) and 431 Districts. In order to segement the Districts and explore them, we will essentially need a dataset that contains the states and the districts that exist in each state as well as the the latitude and logitude coordinates of each districts centroid. 

This dataset exists in kaggle. Dataset can be found in https://www.kaggle.com/sirpunch/indian-census-data-with-geospatial-indexing#district%20wise%20population%20and%20centroids.csv.
However , the data for the project is already downloaded and saved in Github

#### Load and explore the data

In [31]:
import pandas as pd
india=pd.read_csv('https://raw.githubusercontent.com/AmitLinde/Coursera_Capstone/master/Cities.csv')
print(india.shape)
india.head()

(431, 6)


State       District   Latitude  Longitude  Population in 2001  \
0  Andhra Pradesh      Anantapur  14.312066  77.460158             3640478   
1  Andhra Pradesh       Chittoor  13.331093  78.927639             3745875   
2  Andhra Pradesh  East Godavari  16.782718  82.243207             4901420   
3  Andhra Pradesh         Guntur  15.884926  80.586576             4465144   
4  Andhra Pradesh        Krishna  16.143873  81.148051             4187841   

   Population in 2011  
0             4081148  
1             4174064  
2             5154296  
3             4887813  
4             4517398

In [32]:
print('The dataframe has {} states and {} districts.'.format(
len(india['State'].unique()),
india.shape[0]
)
)

The dataframe has 25 states and 431 districts.


### Select districs with most populations

In [33]:
districts = india[['State', 'District', 'Latitude', 'Longitude','Population in 2011']].sort_values(by=['Population in 2011'],ascending=False).head(20).reset_index()
districts

index           State       District   Latitude  Longitude  \
0     261     Maharashtra          Thane  19.698768  72.798827   
1     255     Maharashtra           Pune  18.516962  74.129229   
2     428     West Bengal    Murshidabad  24.259507  88.168169   
3     322       Rajasthan         Jaipur  27.033459  75.771173   
4     252     Maharashtra         Nashik  20.266913  74.038242   
5     108         Gujarat          Surat  21.257614  72.934887   
6     363   Uttar Pradesh      Allahabad  25.392039  82.051724   
7      65           Bihar          Patna  25.402971  85.319843   
8     429     West Bengal          Nadia  23.564110  88.582930   
9       2  Andhra Pradesh  East Godavari  16.782718  82.243207   
10      3  Andhra Pradesh         Guntur  15.884926  80.586576   
11     62           Bihar    Muzaffarpur  26.186644  85.327451   
12    160       Karnataka        Belgaum  16.161072  74.723290   
13    408   Uttar Pradesh      Moradabad  28.851770  78.735802   
14    387   Uttar Pradesh      Ghaziabad  28.749973  77.674419   
15    249     Maharashtra         Nagpur  21.196557  79.021662   
16    337      Tamil Nadu        Chennai  13.058099  80.281392   
17    366   Uttar Pradesh       Azamgarh  26.008291  83.012203   
18    401   Uttar Pradesh        Lucknow  26.838234  80.897060   
19      4  Andhra Pradesh        Krishna  16.143873  81.148051   

    Population in 2011  
0             11060148  
1              9429408  
2              7103807  
3              6626178  
4              6107187  
5              6081322  
6              5954391  
7              5838465  
8              5167600  
9              5154296  
10             4887813  
11             4801062  
12             4779661  
13             4772006  
14             4681645  
15             4653570  
16             4646732  
17             4613913  
18             4589838  
19             4517398

In [34]:
print('The dataframe has {} states and {} districts.'.format(
len(districts['State'].unique()),
districts.shape[0]
)
)

The dataframe has 9 states and 20 districts.


####  Use geopy library to get the latitude and longitude values of India.

In [35]:
address = 'India'
geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate for centroid of India are {}, {}.'.format(latitude, longitude
))

The geograpical coordinate for centroid of India are 22.3511148, 78.6677428.


# create map of India using latitude and longitude values
map_india = folium.Map(location=[latitude, longitude], zoom_start=10)
# add markers to map
for lat, lng, State, District in zip(india['Latitude'], india['Longitude'], india['State'], india['District']):
    label = '{}, {}'.format(District, State)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_india)
map_india

Next, we are going to start utilizing the Foursquare API to explore the neighborhoods and segment them.

#### Define Foursquare Credentials and Version

In [49]:
CLIENT_ID = 'HT4J1D0RWL52AV4QMEJ2DE0A0L1NWSUYRIVURPOTOXY04OAY' # your Foursquare ID
CLIENT_SECRET = 'J5QCUFEICHUV5NFJVKI1STS2M1WXSQOVJ3CBQR3KMI0CY0FM' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: HT4J1D0RWL52AV4QMEJ2DE0A0L1NWSUYRIVURPOTOXY04OAY
CLIENT_SECRET:J5QCUFEICHUV5NFJVKI1STS2M1WXSQOVJ3CBQR3KMI0CY0FM


#### Let's explore the first district in our dataframe.
Get the district's name.

In [50]:
districts.loc[0, 'District']

'Thane'

Get the Districts's latitude and longitude values.

In [51]:
neighborhood_latitude = districts.loc[0, 'Latitude'] # neighborhood latitude value
neighborhood_longitude = districts.loc[0, 'Longitude'] # neighborhood longitude value

neighborhood_name = districts.loc[0, 'District'] # neighborhood name

print('Latitude and longitude values of {} are {}, {}.'.format(neighborhood_name, 
                                                               neighborhood_latitude, 
                                                               neighborhood_longitude))

Latitude and longitude values of Thane are 19.698767747440268, 72.79882742564581.


#### Now, let's get the top 25 venues that are within a radius of 50,000 meters of above co-ordinates

First, let's create the GET request URL. Name your URL **url**.

In [74]:
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    'HT4J1D0RWL52AV4QMEJ2DE0A0L1NWSUYRIVURPOTOXY04OAY', 
    'J5QCUFEICHUV5NFJVKI1STS2M1WXSQOVJ3CBQR3KMI0CY0FM', 
    20200101, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    50000, 
    25)
url # display URL

'https://api.foursquare.com/v2/venues/explore?&client_id=HT4J1D0RWL52AV4QMEJ2DE0A0L1NWSUYRIVURPOTOXY04OAY&client_secret=J5QCUFEICHUV5NFJVKI1STS2M1WXSQOVJ3CBQR3KMI0CY0FM&v=20200101&ll=19.698767747440268,72.79882742564581&radius=50000&limit=25'

Send the GET request and examine the resutls

From the Foursquare lab in the previous module, we know that all the information is in the *items* key. Before we proceed, let's borrow the **get_category_type** function from the Foursquare lab.

In [75]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

Now we are ready to clean the json and structure it into a *pandas* dataframe.

In [76]:
import requests

results = requests.get(url).json()
venues = results['response']['groups'][0]['items']    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.shape

(21, 4)

In [77]:
nearby_venues

name             categories        lat        lng
0         NATURALS ICE-CREAM         Ice Cream Shop  19.447924  72.801314
1      Bhajansons Dairy Farm             Restaurant  19.380189  72.898666
2       Celebrity Restaurant      Indian Restaurant  19.399813  72.840600
3                 Hotel Anam      Indian Restaurant  19.707390  72.921284
4        Silent Hills Resort                   Pool  19.709589  72.932746
5          Shri Datta Snacks         Breakfast Spot  19.684512  72.908546
6                   Pearline             Restaurant  19.991458  72.723237
7                 True Taste             Restaurant  19.377543  72.827801
8                Kelwa Beach                  Beach  19.613246  72.731072
9                     Subway         Sandwich Place  19.258144  72.853034
10                Kandarpada  Outdoors & Recreation  19.259463  72.852927
11               Hotel Ahura      Indian Restaurant  20.017882  72.924604
12                McDonald's   Fast Food Restaurant  19.678694  72.908230
13                Crazy crab                  Diner  20.088340  72.733646
14              Hotel Atithi   Fast Food Restaurant  19.908049  72.939134
15     Pearline Beach Resort             Restaurant  19.991465  72.723260
16  vaitarna railway station          Train Station  19.515867  72.850276
17         Dahanu Road Beach     Seafood Restaurant  19.987089  72.721645
18              Dahanu Beach                  Beach  19.991990  72.586809
19                      Wada            Bus Station  19.652950  73.131921
20               Bordi Beach                  Beach  20.109571  72.737987

In [78]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

21 venues were returned by Foursquare.


## 2.  Explore Neighborhoods in Indian States

In [ ]:
#### Let's create a function to repeat the same process to all the neighborhoods 

In [79]:
def getNearbyVenues(names, latitudes, longitudes, radius=50000,LIMIT=25):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            'HT4J1D0RWL52AV4QMEJ2DE0A0L1NWSUYRIVURPOTOXY04OAY', 
            'J5QCUFEICHUV5NFJVKI1STS2M1WXSQOVJ3CBQR3KMI0CY0FM', 
            20200101, 
            lat, 
            lng, 
            50000, 
            25)
            
        # make the GET request
        results = requests.get(url).json()['response']['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

#### Now  the code to run the above function on each District and create a new dataframe called *india_venues*.

In [80]:
india_venues = getNearbyVenues(names=india['District'],
                                   latitudes=india['Latitude'],
                                   longitudes=india['Longitude']
                                )    

Anantapur
Chittoor
East Godavari
Guntur
Krishna
Kurnool
Prakasam
Srikakulam
Vizianagaram
West Godavari
Changlang
East Kameng
East Siang
Kurung Kumey
Lohit
Lower Dibang Valley
Lower Subansiri
Papum Pare
Tawang
Tirap
Upper Siang
Upper Subansiri
West Kameng
West Siang
Barpeta
Bongaigaon
Cachar
Darrang
Dhemaji
Dibrugarh
Goalpara
Golaghat
Hailakandi
Jorhat
Kamrup
Karbi Anglong
Karimganj
Kokrajhar
Lakhimpur
Nagaon
Nalbari
Sonitpur
Tinsukia
Araria
Aurangabad
Banka
Begusarai
Bhagalpur
Bhojpur
Buxar
Darbhanga
Gaya
Gopalganj
Jamui
Jehanabad
Katihar
Khagaria
Kishanganj
Lakhisarai
Madhepura
Madhubani
Munger
Muzaffarpur
Nalanda
Nawada
Patna
Purnia
Rohtas
Saharsa
Samastipur
Saran
Sheikhpura
Sheohar
Sitamarhi
Siwan
Supaul
Vaishali
Chandigarh
Bastar
Bilaspur
Dhamtari
Durg
Janjgir-Champa
Jashpur
Korba
Koriya
Mahasamund
Raigarh
Raipur
Surguja
North Goa
South Goa
Amreli
Anand
Banas Kantha
Bharuch
Bhavnagar
Gandhinagar
Jamnagar
Junagadh
Kachchh
Kheda
Narmada
Navsari
Patan
Porbandar
Rajkot
Sabar Kantha
Sur

In [81]:
india_venues.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0    Anantapur              14.312066               77.460158   
1    Anantapur              14.312066               77.460158   
2    Anantapur              14.312066               77.460158   
3    Anantapur              14.312066               77.460158   
4    Anantapur              14.312066               77.460158   

                                 Venue  Venue Latitude  Venue Longitude  \
0                Hanuman Hillrock Cafe       14.165056        77.812683   
1  Western Canteen ( Foreign Canteen )       14.165920        77.808753   
2                         BIG  Cinemas       14.681915        77.603515   
3                            Sri Sagar       14.678610        77.601763   
4                 Hotel Masineni Grand       14.678782        77.602078   

                  Venue Category  
0  Vegetarian / Vegan Restaurant  
1  Vegetarian / Vegan Restaurant  
2                  Movie Theater  
3  Vegetarian / Vegan Restaurant  
4                          Hotel

In [84]:
india_venues.shape

(4669, 7)

In [85]:
india_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  Venue  \
Neighborhood                                                                
Agra                                    25                      25     25   
Aizawl                                   5                       5      5   
Ajmer                                   25                      25     25   
Akola                                   10                      10     10   
Alappuzha                               25                      25     25   
Aligarh                                 15                      15     15   
Allahabad                               19                      19     19   
Alwar                                    6                       6      6   
Ambala                                  25                      25     25   
Ambedkar Nagar                           4                       4      4   
Amravati                                 7                       7      7   
Amreli                                   4                       4      4   
Amritsar                                25                      25     25   
Anand                                   17                      17     17   
Anantapur                                5                       5      5   
Anuppur                                  6                       6      6   
Araria                                   4                       4      4   
Ariyalur                                16                      16     16   
Ashoknagar                               4                       4      4   
Auraiya                                 11                      11     11   
Aurangabad                              34                      34     34   
Azamgarh                                 8                       8      8   
Bagalkot                                 9                       9      9   
Baghpat                                 25                      25     25   
Bahraich                                 6                       6      6   
Balaghat                                 7                       7      7   
Ballia                                   7                       7      7   
Balrampur                                4                       4      4   
Banas Kantha                             4                       4      4   
Banda                                    4                       4      4   
Bangalore Rural                         25                      25     25   
Banka                                    8                       8      8   
Bankura                                  3                       3      3   
Banswara                                 3                       3      3   
Bara Banki                              25                      25     25   
Baran                                    5                       5      5   
Bareilly                                 4                       4      4   
Barmer                                   5                       5      5   
Barpeta                                  6                       6      6   
Barwani                                  4                       4      4   
Bastar                                   5                       5      5   
Basti                                    8                       8      8   
Bathinda                                 9                       9      9   
Begusarai                                4                       4      4   
Belgaum                                 25                      25     25   
Bellary                                 25                      25     25   
Betul                                    6                       6      6   
Bhagalpur                                2                       2      2   
Bhandara                                 5                       5      5   
Bharatpur                               11                      11     11   
Bharuch          

#### Let's find out how many unique categories can be curated from all the returned venues

In [87]:
print('There are {} uniques categories.'.format(len(india_venues['Venue Category'].unique())))

There are 250 uniques categories.


## 3. Analyze Each Neighborhood

In [89]:
# one hot encoding
india_onehot = pd.get_dummies(india_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
india_onehot['Neighborhood'] = india_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [india_onehot.columns[-1]] + list(india_onehot.columns[:-1])
india_onehot = india_onehot[fixed_columns]

india_onehot.head()

Zoo  ATM  Afghan Restaurant  Airport  Airport Food Court  Airport Service  \
0    0    0                  0        0                   0                0   
1    0    0                  0        0                   0                0   
2    0    0                  0        0                   0                0   
3    0    0                  0        0                   0                0   
4    0    0                  0        0                   0                0   

   Airport Terminal  American Restaurant  Arcade  Art Gallery  Art Museum  \
0                 0                    0       0            0           0   
1                 0                    0       0            0           0   
2                 0                    0       0            0           0   
3                 0                    0       0            0           0   
4                 0                    0       0            0           0   

   Arts & Crafts Store  Asian Restaurant  Astrologer  Athletics & Sports  \
0                    0                 0           0                   0   
1                    0                 0           0                   0   
2                    0                 0           0                   0   
3                    0                 0           0                   0   
4                    0                 0           0                   0   

   Auto Garage  BBQ Joint  Badminton Court  Bakery  Bank  Bar  Beach  \
0            0          0                0       0     0    0      0   
1            0          0                0       0     0    0      0   
2            0          0                0       0     0    0      0   
3            0          0                0       0     0    0      0   
4            0          0                0       0     0    0      0   

   Bed & Breakfast  Bengali Restaurant  Big Box Store  Bike Shop  Bistro  \
0                0                   0              0          0       0   
1                0                   0              0          0       0   
2                0                   0              0          0       0   
3                0                   0              0          0       0   
4                0                   0              0          0       0   

   Boarding House  Boat or Ferry  Bookstore  Border Crossing  \
0               0              0          0                0   
1               0              0          0                0   
2               0              0          0                0   
3               0              0          0                0   
4               0              0          0                0   

   Botanical Garden  Bowling Alley  Brazilian Restaurant  Breakfast Spot  \
0                 0              0                     0               0   
1                 0              0                     0               0   
2                 0              0                     0               0   
3                 0              0                     0               0   
4                 0              0                     0               0   

   Brewery  Bubble Tea Shop  Buddhist Temple  Buffet  Burger Joint  \
0        0                0                0       0             0   
1        0                0                0       0             0   
2        0                0                0       0             0   
3        0                0                0       0             0   
4        0                0                0       0             0   

   Bus Station  Business Service  Cafeteria  Café  Campground  Canal Lock  \
0            0                 0          0     0           0           0   
1            0                 0          0     0           0           0   
2            0                 0          0     0           0           0   
3            0                 0          0     0           0           0   
4            0                 0          0     0           0   

In [90]:
india_onehot.shape

(4669, 250)

#### Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [91]:
india_grouped = india_onehot.groupby('Neighborhood').mean().reset_index()
india_grouped

Neighborhood       Zoo       ATM  Afghan Restaurant   Airport  \
0                   Agra  0.000000  0.000000               0.00  0.000000   
1                 Aizawl  0.000000  0.000000               0.00  0.000000   
2                  Ajmer  0.000000  0.000000               0.00  0.000000   
3                  Akola  0.000000  0.200000               0.00  0.000000   
4              Alappuzha  0.000000  0.000000               0.00  0.000000   
5                Aligarh  0.000000  0.000000               0.00  0.000000   
6              Allahabad  0.000000  0.000000               0.00  0.052632   
7                  Alwar  0.000000  0.000000               0.00  0.000000   
8                 Ambala  0.000000  0.000000               0.00  0.000000   
9         Ambedkar Nagar  0.000000  0.250000               0.00  0.000000   
10              Amravati  0.000000  0.000000               0.00  0.000000   
11                Amreli  0.000000  0.000000               0.00  0.000000   
12              Amritsar  0.000000  0.000000               0.00  0.000000   
13                 Anand  0.000000  0.000000               0.00  0.000000   
14             Anantapur  0.000000  0.000000               0.00  0.000000   
15               Anuppur  0.000000  0.833333               0.00  0.000000   
16                Araria  0.000000  0.250000               0.00  0.000000   
17              Ariyalur  0.000000  0.000000               0.00  0.000000   
18            Ashoknagar  0.000000  0.500000               0.00  0.000000   
19               Auraiya  0.000000  0.363636               0.00  0.000000   
20            Aurangabad  0.000000  0.088235               0.00  0.029412   
21              Azamgarh  0.000000  0.375000               0.00  0.000000   
22              Bagalkot  0.000000  0.000000               0.00  0.000000   
23               Baghpat  0.000000  0.000000               0.00  0.000000   
24              Bahraich  0.000000  0.000000               0.00  0.000000   
25              Balaghat  0.000000  0.000000               0.00  0.000000   
26                Ballia  0.000000  0.714286               0.00  0.000000   
27             Balrampur  0.000000  0.000000               0.00  0.000000   
28          Banas Kantha  0.000000  0.000000               0.00  0.000000   
29                 Banda  0.000000  0.250000               0.00  0.000000   
30       Bangalore Rural  0.000000  0.000000               0.00  0.000000   
31                 Banka  0.000000  0.375000               0.00  0.000000   
32               Bankura  0.000000  0.666667               0.00  0.000000   
33              Banswara  0.000000  0.000000               0.00  0.000000   
34            Bara Banki  0.000000  0.000000               0.00  0.000000   
35                 Baran  0.000000  0.400000               0.00  0.000000   
36              Bareilly  0.000000  0.000000               0.00  0.000000   
37                Barmer  0.000000  0.000000               0.00  0.000000   
38               Barpeta  0.000000  0.000000               0.00  0.000000   
39               Barwani  0.000000  0.250000               0.00  0.000000   
40                Bastar  0.000000  0.400000               0.00  0.000000   
41                 Basti  0.000000  0.500000               0.00  0.000000   
42              Bathinda  0.000000  0.000000               0.00  0.000000   
43             Begusarai  0.000000  0.000000               0.00  0.000000   
44               Belgaum  0.000000  0.000000               0.00  0.040000   
45               Bellary  0.000000  0.000000               0.00  0.000000   
46                 Betul  0.000000  0.333333               0.00  0.000000   
47             Bhagalpur  0.000000  0.000000               0.00  0.000000   
48              Bhandara  0.000000  0.000000               0.00  0.000000   
49             Bharatpur  0.000000  0.000000               0.00  0.000000   
50               Bharuch  0.000000  0.000000               0.00  0.000000   
51      

In [92]:
## lets confirm the new size
india_grouped.shape

(422, 250)

#### Let's print each neighborhood along with the top 5 most common venues

In [95]:
num_top_venues = 5

for hood in india_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = india_grouped[india_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Agra----
                            venue  freq
0                           Hotel  0.28
1               Indian Restaurant  0.20
2                   Historic Site  0.12
3                          Resort  0.08
4  Multicuisine Indian Restaurant  0.08


----Aizawl----
           venue  freq
0          Hotel   0.4
1  Shopping Mall   0.2
2           Park   0.2
3     Soup Place   0.2
4         Office   0.0


----Ajmer----
               venue  freq
0               Café  0.16
1  Indian Restaurant  0.16
2              Hotel  0.16
3        Pizza Place  0.12
4               Lake  0.08


----Akola----
               venue  freq
0  Mobile Phone Shop   0.7
1                ATM   0.2
2       Dessert Shop   0.1
3             Palace   0.0
4      National Park   0.0


----Alappuzha----
               venue  freq
0             Resort  0.44
1  Indian Restaurant  0.12
2              Hotel  0.08
3               Lake  0.04
4       Dessert Shop  0.04


----Aligarh----
                     venue  freq
0  

#### Let's put that into a *pandas* dataframe
First, let's write a function to sort the venues in descending order.

In [96]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

Now let's create the new dataframe and display the top 10 venues for each neighborhood.

In [100]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = india_grouped['Neighborhood']

for ind in np.arange(india_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(india_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0         Agra                 Hotel     Indian Restaurant   
1       Aizawl                 Hotel         Shopping Mall   
2        Ajmer     Indian Restaurant                  Café   
3        Akola     Mobile Phone Shop                   ATM   
4    Alappuzha                Resort     Indian Restaurant   

  3rd Most Common Venue 4th Most Common Venue           5th Most Common Venue  \
0         Historic Site  Fast Food Restaurant  Multicuisine Indian Restaurant   
1            Soup Place                  Park                            Food   
2                 Hotel           Pizza Place   Vegetarian / Vegan Restaurant   
3          Dessert Shop           Yoga Studio               Fondue Restaurant   
4                 Hotel                  Lake                            Café   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0                Resort                Garden   Fried Chicken Joint   
1  Fast Food Restaurant                 Field           Flea Market   
2                  Lake  Fast Food Restaurant                  City   
3                  Food     Food & Drink Shop            Food Court   
4        General Travel            Restaurant            Lighthouse   

  9th Most Common Venue 10th Most Common Venue  
0                  Pool        Bed & Breakfast  
1     Fondue Restaurant            Yoga Studio  
2                Bakery                 Resort  
3            Food Truck      French Restaurant  
4                 Beach         Scenic Lookout

## 4. Cluster Neighborhoods

Run *k*-means to cluster the neighborhood into 5 clusters.

In [102]:
# set number of clusters
kclusters = 5

india_grouped_clustering = india_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(india_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([3, 2, 3, 1, 3, 2, 2, 3, 2, 4], dtype=int32)

Let's create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.

In [125]:
# add clustering labels
# neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

india_merged = india[['State','District','Latitude','Longitude']]

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
india_merged = india_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='District')

india_merged.head() # check the last columns

State       District   Latitude  Longitude  Cluster Labels  \
0  Andhra Pradesh      Anantapur  14.312066  77.460158             2.0   
1  Andhra Pradesh       Chittoor  13.331093  78.927639             3.0   
2  Andhra Pradesh  East Godavari  16.782718  82.243207             3.0   
3  Andhra Pradesh         Guntur  15.884926  80.586576             3.0   
4  Andhra Pradesh        Krishna  16.143873  81.148051             3.0   

           1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0  Vegetarian / Vegan Restaurant         Movie Theater                 Hotel   
1              Indian Restaurant                  Café           Pizza Place   
2                      Multiplex     Indian Restaurant           Pizza Place   
3                 Ice Cream Shop                 Hotel     Indian Restaurant   
4                          Beach     Indian Restaurant         Movie Theater   

  4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0           Yoga Studio            Food Court           Flea Market   
1         Historic Site                 Hotel           Snack Place   
2   Fried Chicken Joint                Bakery                Lounge   
3         Movie Theater                 Beach   Indie Movie Theater   
4        Cosmetics Shop           Yoga Studio                Forest   

  7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0     Fondue Restaurant                  Food     Food & Drink Shop   
1          Burger Joint           Bus Station    Chinese Restaurant   
2      Asian Restaurant                 Hotel           Coffee Shop   
3                Market         Train Station           Flea Market   
4                  Food     Food & Drink Shop            Food Court   

    10th Most Common Venue  
0                   Forest  
1  South Indian Restaurant  
2         Department Store  
3        Fondue Restaurant  
4               Food Truck

## 5. Examine Clusters

Now, you can examine each cluster and determine the discriminating venue categories that distinguish each cluster. Based on the defining categories, you can then assign a name to each cluster. I will leave this exercise to you.

## Cluster1

In [127]:
india_merged.loc[india_merged['Cluster Labels'] == 0, india_merged.columns[[1] + list(range(5, india_merged.shape[1]))]]

District 1st Most Common Venue    2nd Most Common Venue  \
21    Upper Subansiri                   ATM              Yoga Studio   
23         West Siang                   ATM              Yoga Studio   
25         Bongaigaon                   ATM            Train Station   
26             Cachar                   ATM         Airport Terminal   
41           Sonitpur                   ATM        Indian Restaurant   
45              Banka                   ATM              Pizza Place   
50          Darbhanga                   ATM            Shopping Mall   
58         Lakhisarai                   ATM            Train Station   
59          Madhepura                   ATM              Yoga Studio   
60          Madhubani                   ATM                  Airport   
67             Rohtas                   ATM            Train Station   
75             Supaul                   ATM             Dessert Shop   
78             Bastar                   ATM        Electronics Store   
83            Jashpur                   ATM              Bus Station   
86         Mahasamund                   ATM          Motorcycle Shop   
88             Raipur                   ATM              Yoga Studio   
89            Surguja                   ATM            Train Station   
114           Bhiwani                   ATM                    Dhaba   
116         Fatehabad                   ATM            Train Station   
120              Jind                   ATM        Indian Restaurant   
142            Chatra                   ATM                     Café   
145             Dumka                   ATM              Bus Station   
146            Garhwa                   ATM           Clothing Store   
148             Godda                   ATM               Restaurant   
151           Latehar                   ATM           Scenic Lookout   
152         Lohardaga                   ATM           Scenic Lookout   
154            Palamu                   ATM           Clothing Store   
163           Bijapur                   ATM  Comfort Food Restaurant   
193           Anuppur                   ATM        Electronics Store   
194        Ashoknagar                   ATM                    River   
198             Bhind                   ATM              IT Services   
214            Jhabua                   ATM           Ice Cream Shop   
220             Panna                   ATM   Furniture / Home Store   
222           Rajgarh    Light Rail Station                      ATM   
226             Satna                   ATM     Fast Food Restaurant   
228             Seoni                   ATM              Yoga Studio   
229           Shahdol                   ATM                    Hotel   
266           Chandel                   ATM              IT Services   
274     Jaintia Hills                   ATM              Yoga Studio   
277  West Khasi Hills            Campground                      ATM   
281         Lawngtlai                 Trail                      ATM   
284             Saiha                   ATM  Health & Beauty Service   
285          Serchhip                   ATM                     Lake   
286           Dimapur                   ATM                  Airport   
312             Baran                   ATM    Rajasthani Restaurant   
318             Churu                   ATM           Shopping Plaza   
365           Auraiya                   ATM        Indian Restaurant   
366          Azamgarh                   ATM        Convenience Store   
369            Ballia                   ATM            Train Station   
374             Basti                   ATM            Train Station   
379            Deoria                   ATM        Currency Exchange   
380              Etah                   ATM           Clothing Store   
383       Farrukhabad                   ATM        Indian Restaurant   
394           Jaunpur                   ATM         Airport Terminal   
396           Kannauj                   ATM        In

## Cluster 2

In [128]:
india_merged.loc[india_merged['Cluster Labels'] == 1, india_merged.columns[[1] + list(range(5, india_merged.shape[1]))]]

District 1st Most Common Venue 2nd Most Common Venue  \
233      Sidhi     Mobile Phone Shop                   ATM   
238      Akola     Mobile Phone Shop                   ATM   
243      Dhule                   ATM        Breakfast Spot   
244    Hingoli     Mobile Phone Shop                   ATM   
246      Jalna     Mobile Phone Shop                   ATM   
251  Nandurbar                   ATM     Mobile Phone Shop   
253  Osmanabad     Mobile Phone Shop         Train Station   
254   Parbhani     Mobile Phone Shop         Train Station   
260    Solapur     Mobile Phone Shop                   ATM   
263     Washim     Mobile Phone Shop     Indian Restaurant   
264   Yavatmal     Mobile Phone Shop        Clothing Store   
271     Ukhrul                   ATM     Mobile Phone Shop   
291   Tuensang              Mountain     Mobile Phone Shop   

        3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
233            Scenic Lookout           Yoga Studio           Flea Market   
238              Dessert Shop           Yoga Studio     Fondue Restaurant   
243      Fast Food Restaurant     Mobile Phone Shop           Yoga Studio   
244         Indian Restaurant                Forest     Fondue Restaurant   
246                     Hotel         Train Station           Yoga Studio   
251                      Café           Yoga Studio           Flea Market   
253               Yoga Studio  Fast Food Restaurant           Gaming Cafe   
254                       ATM              Platform           Yoga Studio   
260  Maharashtrian Restaurant         Train Station           Yoga Studio   
263               Yoga Studio                 Field                Garden   
264                      Café           Yoga Studio           Flea Market   
271                Campground           Yoga Studio           Flea Market   
291               Yoga Studio           Gas Station                Garden   

      6th Most Common Venue   7th Most Common Venue   8th Most Common Venue  \
233       Fondue Restaurant                    Food       Food & Drink Shop   
238                    Food       Food & Drink Shop              Food Court   
243                  Forest                    Food       Food & Drink Shop   
244                    Food       Food & Drink Shop              Food Court   
246             Flea Market       Fondue Restaurant                    Food   
251                  Garden             Gaming Cafe  Furniture / Home Store   
253  Furniture / Home Store     Fried Chicken Joint       French Restaurant   
254              Food Truck             Flea Market       Fondue Restaurant   
260       Fondue Restaurant                    Food       Food & Drink Shop   
263             Gaming Cafe  Furniture / Home Store     Fried Chicken Joint   
264                  Garden             Gaming Cafe  Furniture / Home Store   
271                  Garden             Gaming Cafe  Furniture / Home Store   
291             Gaming Cafe  Furniture / Home Store     Fried Chicken Joint   

    9th Most Common Venue 10th Most Common Venue  
233            Food Court             Food Truck  
238            Food Truck      French Restaurant  
243            Food Court             Food Truck  
244            Food Truck            Yoga Studio  
246     Food & Drink Shop             Food Court  
251   Fried Chicken Joint      French Restaurant  
253                Forest             Food Truck  
254                  Food      Food & Drink Shop  
260            Food Court             Food Truck  
263     French Restaurant                 Forest  
264   Fried Chicken Joint      French Restaurant  
271   Fried Chicken Joint      French Restaurant  
291     French Restaurant                 Forest

## Cluster 3

In [129]:
india_merged.loc[india_merged['Cluster Labels'] == 2, india_merged.columns[[1] + list(range(5, india_merged.shape[1]))]]

District          1st Most Common Venue  \
0              Anantapur  Vegetarian / Vegan Restaurant   
6               Prakasam                     Food Court   
10             Changlang                  National Park   
12            East Siang                           Cave   
14                 Lohit                  Movie Theater   
15   Lower Dibang Valley                     Campground   
16       Lower Subansiri                     Campground   
17            Papum Pare                 Ice Cream Shop   
18                Tawang                       Mountain   
19                 Tirap                 Scenic Lookout   
20           Upper Siang   Theme Park Ride / Attraction   
22           West Kameng                          Hotel   
27               Darrang                 Ice Cream Shop   
28               Dhemaji                    Gas Station   
29             Dibrugarh                  Train Station   
31              Golaghat                  National Park   
32            Hailakandi                  Shopping Mall   
33                Jorhat      Indian Chinese Restaurant   
34                Kamrup                 Clothing Store   
36             Karimganj                  Shopping Mall   
38             Lakhimpur                 Ice Cream Shop   
40               Nalbari                    Coffee Shop   
42              Tinsukia                         Market   
44            Aurangabad                            ATM   
47             Bhagalpur                    Pizza Place   
51                  Gaya                         Temple   
52             Gopalganj              Convenience Store   
54             Jehanabad                       Platform   
62           Muzaffarpur                 Clothing Store   
63               Nalanda                  Train Station   
64                Nawada                  Train Station   
65                 Patna                           Café   
70                 Saran                           Café   
73             Sitamarhi                         Market   
74                 Siwan              Currency Exchange   
76              Vaishali                           Café   
77            Chandigarh              Indian Restaurant   
81                  Durg                           Café   
87               Raigarh                          Hotel   
90             North Goa                          Hotel   
91             South Goa                          Beach   
92                Amreli                 Ice Cream Shop   
93                 Anand           Fast Food Restaurant   
95               Bharuch                          Hotel   
96             Bhavnagar               Asian Restaurant   
97           Gandhinagar                      Multiplex   
98              Jamnagar                          Hotel   
99              Junagadh                          Hotel   
101                Kheda           Fast Food Restaurant   
102              Narmada            Monument / Landmark   
103              Navsari             Chinese Restaurant   
104                Patan                  Memorial Site   
105            Porbandar                          Beach   
111             Vadodara           Fast Food Restaurant   
113               Ambala              Indian Restaurant   
115            Faridabad                           Café   
117              Gurgaon                          Hotel   
119              Jhajjar                          Hotel   
121              Kaithal           Fast Food Restaurant   
129                Sirsa                 Clothing Store   
131               Chamba                           Café   
133               Kangra             Italian Restaurant   
134              Kinnaur                     Campground   
135                Kullu                           Café   
136                Mandi                 Scenic Lookout   
137               Shimla                          Hotel   
139                Solan                          Hotel   
140 

## Cluster 4

In [130]:
india_merged.loc[india_merged['Cluster Labels'] == 3, india_merged.columns[[1] + list(range(5, india_merged.shape[1]))]]

District 1st Most Common Venue           2nd Most Common Venue  \
1              Chittoor     Indian Restaurant                            Café   
2         East Godavari             Multiplex               Indian Restaurant   
3                Guntur        Ice Cream Shop                           Hotel   
4               Krishna                 Beach               Indian Restaurant   
8          Vizianagaram     Indian Restaurant                   Train Station   
68              Saharsa              Platform               Convenience Store   
79             Bilaspur     Indian Restaurant                            Café   
80             Dhamtari     Indian Restaurant                             ATM   
94         Banas Kantha     Indian Restaurant                   Memorial Site   
100             Kachchh     Indian Restaurant                   Historic Site   
106              Rajkot     Indian Restaurant            Fast Food Restaurant   
107        Sabar Kantha                   Bar                           Hotel   
108               Surat     Indian Restaurant              Chinese Restaurant   
109       Surendranagar  Fast Food Restaurant               Indian Restaurant   
110           The Dangs                Resort                        Mountain   
112              Valsad     Indian Restaurant                     Pizza Place   
122              Karnal  Fast Food Restaurant               Indian Restaurant   
123         Kurukshetra     Indian Restaurant                     Pizza Place   
124        Mahendragarh     Indian Restaurant                   Shopping Mall   
125           Panchkula     Indian Restaurant                          Bakery   
126             Panipat     Indian Restaurant                           Dhaba   
127              Rewari     Indian Restaurant            Fast Food Restaurant   
128              Rohtak           Pizza Place                       Multiplex   
130            Bilaspur     Indian Restaurant                            Café   
138             Sirmaur                  Café               Indian Restaurant   
161             Bellary     Indian Restaurant                   Historic Site   
162               Bidar            Shoe Store               Indian Restaurant   
165          Davanagere     Indian Restaurant                     Coffee Shop   
166             Dharwad     Indian Restaurant                  Breakfast Spot   
170              Haveri     Indian Restaurant                     Coffee Shop   
171              Kodagu                Resort               Indian Restaurant   
173              Koppal     Indian Restaurant                   Historic Site   
178              Tumkur           Coffee Shop                            Café   
179               Udupi     Indian Restaurant            Fast Food Restaurant   
180           Alappuzha                Resort               Indian Restaurant   
183              Kannur     Indian Restaurant                   Shopping Mall   
184           Kasaragod     Indian Restaurant                   Shopping Mall   
187           Kozhikode     Indian Restaurant                   Movie Theater   
188          Malappuram     Indian Restaurant                   Movie Theater   
190  Thiruvananthapuram     Indian Restaurant                           Beach   
192             Wayanad                Resort               Indian Restaurant   
199              Bhopal     Indian Restaurant                          Bakery   
205               Dewas           Snack Place                             ATM   
216              Mandla                  Park                           Trail   
227              Sehore           Pizza Place               Indian Restaurant   
230            Shajapur     Indian Restaurant                   Train Station   
239            Amravati                  Café                       Multiplex   
245             Jalgaon     Indian Restaurant                      Food Truck   
247            Kolhapur     Indian Restaurant 

## Cluster 5

In [131]:
india_merged.loc[india_merged['Cluster Labels'] == 4, india_merged.columns[[1] + list(range(5, india_merged.shape[1]))]]

District 1st Most Common Venue 2nd Most Common Venue  \
5             Kurnool         Train Station             Multiplex   
7          Srikakulam         Train Station              Pharmacy   
9       West Godavari         Train Station                Bakery   
24            Barpeta         Train Station             Gastropub   
30           Goalpara         Train Station                 Hotel   
35      Karbi Anglong         Train Station            Restaurant   
37          Kokrajhar         Train Station                  Farm   
39             Nagaon         Train Station         National Park   
43             Araria           Auto Garage                   ATM   
46          Begusarai         Train Station           Yoga Studio   
48            Bhojpur                   ATM         Train Station   
49              Buxar         Train Station                   ATM   
53              Jamui         Train Station                   ATM   
55            Katihar                   ATM         Train Station   
56           Khagaria                   ATM         Train Station   
57         Kishanganj                   ATM                 Hotel   
61             Munger         Train Station           Pizza Place   
66             Purnia         Train Station                   ATM   
69         Samastipur         Train Station        General Travel   
71         Sheikhpura         Train Station            Hot Spring   
72            Sheohar         Train Station             Multiplex   
82     Janjgir-Champa         Train Station         Shopping Mall   
84              Korba        Clothing Store                   ATM   
85             Koriya         Train Station           Yoga Studio   
118             Hisar         Train Station           Bus Station   
132          Hamirpur         Train Station                 Hotel   
141            Bokaro         Train Station                Market   
143           Deoghar         Train Station                   ATM   
144           Dhanbad         Train Station           Pizza Place   
147           Giridih         Train Station                   ATM   
150           Jamtara         Train Station           Bus Station   
153             Pakur         Train Station           Summer Camp   
156         Sahibganj         Train Station                   ATM   
167             Gadag         Train Station           Bus Station   
168          Gulbarga         Train Station     Mobile Phone Shop   
176           Raichur         Train Station        Mattress Store   
197             Betul         Train Station                   ATM   
200         Burhanpur         Train Station     Mobile Phone Shop   
203             Damoh         Train Station   Rental Car Location   
204             Datia         Train Station                   ATM   
210             Harda         Train Station                   ATM   
211       Hoshangabad         Train Station  Fast Food Restaurant   
215             Katni         Train Station              Platform   
217          Mandsaur         Train Station       Motorcycle Shop   
223            Ratlam         Train Station                  Café   
235            Ujjain         Train Station       Bed & Breakfast   
237           Vidisha         Train Station        Ice Cream Shop   
241          Bhandara         Train Station               Factory   
242        Chandrapur         Train Station                 Hotel   
256         Ratnagiri         Train Station     Indian Restaurant   
262            Wardha         Train Station     Indian Restaurant   
304             Mansa         Train Station                   ATM   
324          Jhalawar       Motorcycle Shop         Train Station   
326           Karauli         Train Station                Market   
328            Nagaur         Train Station       Motorcycle Shop   
364    Ambedkar Nagar         Train Station                   ATM   
371             Banda            Hobby Shop                   ATM   
378        

In [133]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(india_merged['Latitude'], india_merged['Longitude'], india_merged['State'], india_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=1,
        #color=rainbow[cluster - 1],
        fill=True,
        fill_color=1,
        #fill_color=rainbow[cluster-1],        
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters